In [26]:
from tikapi import TikAPI, ValidationException, ResponseException
import json
import glob
import os
import re
import pandas as pd

api = TikAPI("")
User = api.user(accountKey="6EjyV4OptbvUz1cKgMTnvbXNH1wKPqLVV42jKlzydbVrFLnb")

_data_path = "./data/"
video_ids_file = _data_path + "video_list.csv"

max_requests_for_each_video = 20
number_of_comment_each_request = 30 #(max possible value is 30)

# Load video IDs

In [27]:
df = pd.read_csv(video_ids_file)
df = df[df["Influencer/tiktoker"]=="Arianna Biella"]


# extract video ids from links
df["id"] = [re.sub("video/", "", re.findall("video/[0-9]{19}", link)[0]) for link in df["Link"]]
print(f"First 5 video ids:\n{df.head(5)['id']}")

df

First 5 video ids:
3    7140954969871600901
4    7140961766028102918
5    7140966608507358470
6    7146956596566854918
Name: id, dtype: object


Influencer/tiktoker Politician          Date  \
3      Arianna Biella        NaN  08. 09. 2022   
4      Arianna Biella        NaN  08. 09. 2022   
5      Arianna Biella        NaN  08. 09. 2022   
6      Arianna Biella        NaN  24. 09. 2022   

                                   Subject  \
3  Personal preferences on proposed issues   
4  Personal preferences on proposed issues   
5  Personal preferences on proposed issues   
6                 RDC / work / criminality   

                                                Link   Done  \
3  https://www.tiktok.com/@ariannabiellas/video/7...  False   
4  https://www.tiktok.com/@ariannabiellas/video/7...  False   
5  https://www.tiktok.com/@ariannabiellas/video/7...  False   
6  https://www.tiktok.com/@ariannabiellas/video/7...  False   

                    id  
3  7140954969871600901  
4  7140961766028102918  
5  7140966608507358470  
6  7146956596566854918

In [ ]:
df[df['id']==""]

In [28]:

j = 0 #single video request counter
total_n_comments_read = 0 #total comments counter

# iterate over videos
for i, row in df.iterrows():
    
    # check if comments to this video have already been downloaded
    if not row['Done']:
        
        id = str(row['id'])
        file = _data_path + row['Influencer/tiktoker'] + "_com_" + id + ".json"
        comments = [] #it will contain all the json responses for each request
        
        print("\n#########################################\nProcessing video",id)

        try:
            response = User.posts.comments.list(
                media_id = id,
                count = number_of_comment_each_request # (max possible value is 30)
            )

            response_json = response.json()
            # print(response_json)
            
            j=1
            while(response):    
                # print(response_json)
                # append response data to result list
                comments.append(response_json['comments'])
                total_n_comments_read += len(response_json['comments'])
                    
                # check if we reached maximum n of requests for this video
                if j >= max_requests_for_each_video:
                    break #stop
                    
                # if not, do next request
                cursor = response.json().get('cursor')
                response = response.next_items()  

                if response == None:
                    break # no more responses

                response_json = response.json()
                
                if response_json['comments'] == None:
                    break #no more comments (?)
                j+=1

        except ValidationException as e:
            print(e, e.field)

        except ResponseException as e:
            print(e, e.response.status_code)

        # remove comments from last response object. Now, only the meta data remains.
        response_json['comments'] = None

        # creat dictionary with metadata and comments
        out = {"meta": response_json, "comments": comments}

        with open(file, 'w') as f:
            json.dump(out, f)



#########################################
Processing video 7140954969871600901
{'alias_comment_deleted': False, 'comments': [{'author_pin': True, 'aweme_id': '7140954969871600901', 'cid': '7140970259323273990', 'collect_stat': 0, 'comment_language': 'it', 'create_time': 1662636746, 'digg_count': 2192, 'is_author_digged': False, 'label_list': None, 'label_text': 'Creator', 'label_type': 1, 'no_show': False, 'reply_comment': None, 'reply_comment_total': 64, 'reply_id': '0', 'reply_to_reply_id': '0', 'share_info': {'acl': {'code': 1, 'extra': '{"item_share_acl":"empty item value"}'}, 'desc': "Arianna Biella's comment: sono opinioni personali che TUTTI siamo liberi di avere🙏 esprimete le vostre con garbo", 'title': "queste sono mie opinioni: sulle questioni morali non c'è giusto o sbagliato. Rispettate sempre le idee degli altri anche quando non siete d'accordo🤍 ", 'url': 'https://m.tiktok.com/v/7140954969871600901.html?_d=e5c561b583004i&comment_author_id=6781009138794169350&language=en&p

{'meta': {'alias_comment_deleted': False,
  'comments': None,
  'cursor': 60,
  'extra': {'fatal_item_ids': None, 'now': 1672412141000},
  'has_more': 0,
  'log_pb': {'impr_id': '202212301455417B65FF14DAEA47F3F789'},
  'message': '',
  'reply_style': 2,
  'status': 'success',
  'status_code': 0,
  'top_gifts': None,
  'total': 122},
 'comments': [[{'author_pin': False,
    'aweme_id': '7146956596566854918',
    'cid': '7147085628814164741',
    'collect_stat': 0,
    'comment_language': 'it',
    'create_time': 1664060570,
    'digg_count': 157,
    'is_author_digged': False,
    'label_list': None,
    'no_show': False,
    'reply_comment': None,
    'reply_comment_total': 7,
    'reply_id': '0',
    'reply_to_reply_id': '0',
    'share_info': {'acl': {'code': 1,
      'extra': '{"item_share_acl":"empty item value"}'},
     'desc': "Robi De Tommasi's comment: In realtà anche per fare un lavoro come il postino richiedono il casellario!",
     'title': 'Risposta a @c ',
     'url': 'htt

# Example for reading data

In [45]:
with open("./data/Arianna Biella_com_7140954969871600901.json") as infile:
    # returns JSON object as 
    # a dictionary
    data = json.load(infile)
data

{'meta': {'alias_comment_deleted': False,
  'comments': None,
  'cursor': 540,
  'extra': {'fatal_item_ids': None, 'now': 1672412098000},
  'has_more': 0,
  'log_pb': {'impr_id': '202212301454586DAE99FC1EA45DE430F7'},
  'message': '',
  'reply_style': 2,
  'status': 'success',
  'status_code': 0,
  'top_gifts': None,
  'total': 510},
 'comments': [[{'author_pin': True,
    'aweme_id': '7140954969871600901',
    'cid': '7140970259323273990',
    'collect_stat': 0,
    'comment_language': 'it',
    'create_time': 1662636746,
    'digg_count': 2192,
    'is_author_digged': False,
    'label_list': None,
    'label_text': 'Creator',
    'label_type': 1,
    'no_show': False,
    'reply_comment': None,
    'reply_comment_total': 64,
    'reply_id': '0',
    'reply_to_reply_id': '0',
    'share_info': {'acl': {'code': 1,
      'extra': '{"item_share_acl":"empty item value"}'},
     'desc': "Arianna Biella's comment: sono opinioni personali che TUTTI siamo liberi di avere🙏 esprimete le vostre

In [46]:
len(data['comments'])

17

In [39]:
os.listdir(_data_path)

['video_ids.txt',
 'Arianna Biella_com_7140961766028102918.json',
 'Arianna Biella_com_7146956596566854918.json',
 'comment_list.json',
 'Salvini_com_7146104387079900421.json',
 'Meloni_com_7144986246215929094.json',
 'Berlusconi_com_7138834940187151622.json',
 'Arianna Biella_com_7140954969871600901.json',
 'video_list.csv',
 'Arianna Biella_com_7140966608507358470.json']

<p style="text-align: center;"> <i><b> Fin </b></i> </p>